# Prévisions de la demande de vélos en libre-service
##### Projet MLDL - Roland, Lina, Maéva

### Sommaire du Projet

1. [Explication du problème de machine learning](#1-problem)
2. [Présentation du jeu de données](#2-data-presentation)
3. [Exploration du jeu de données (EDA)](#3-eda)
4. [Data cleaning et imputation](#4-cleaning)
5. [Feature Engineering](#5-feature-engineering)
6. [Préparation des données pour les modèles ML/DL](#6-preprocessing)
7. [Sélection de différents modèles](#7-model-selection)
8. [Évaluation de la performance des modèles](#8-evaluation)
9. [Discussion autour de la performance](#9-discussion)
10. [Synthèse et conclusions](#10-conclusion)

<a id="0-libs"></a>
### 0. Import des librairies nécéssaires

In [43]:
import sys
import pandas as pd
import numpy as np
import math
from datetime import datetime

import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Configuration du style des graphiques
%matplotlib inline
sns.set_style("whitegrid")
plt.rcParams['figure.figsize'] = (12, 6)

# Preprocessing et Séparation
from sklearn.model_selection import train_test_split, TimeSeriesSplit, GridSearchCV
from sklearn.preprocessing import MinMaxScaler, StandardScaler, RobustScaler
# Métriques d'évaluation
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
# Modèles classiques
from sklearn.linear_model import LinearRegression, Ridge, Lasso
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from statsmodels.tsa.seasonal import DecomposeResult, seasonal_decompose
import xgboost as xgb
import tensorflow as tf
#from tensorflow.keras.models import Sequential
#from tensorflow.keras.layers import Dense, LSTM, GRU, Dropout
#from tensorflow.keras.callbacks import EarlyStopping

import warnings
import joblib  # Pour sauvegarder les modèles en .pkl
import os
import sys
warnings.filterwarnings('ignore')

sys.path.append(os.path.abspath('..'))
from src.utils import plot_seasonal_decompose

<a id="1-problem"></a>
### 1. Explication du problème de machine learning

Les systèmes de vélos en libre-service, déployés aujourd'hui dans plus de 500 villes, agissent comme de véritables capteurs virtuels de la mobilité urbaine grâce à l'enregistrement précis des trajets.

C'est dans ce contexte que nous avons choisi d'analyser le **Bike Sharing Dataset**, issu du *UCI Machine Learning Repository*. Ce jeu de données regroupe l'historique des locations de vélos à Washington D.C., enrichi de **données contextuelles exogènes** essentielles telles que les conditions météorologiques (température, humidité) et les informations calendaires (jours fériés, vacances).

Dans ce projet, nous abordons une problématique de **régression supervisée sur série temporelle** visant à anticiper les flux de déplacements.

L'objectif principal est de prédire la demande horaire de vélos (variable cible `cnt`) à un horizon futur défini. Pour y parvenir, nous mettrons en œuvre et comparerons des algorithmes de **Machine Learning** (ex: XGBoost) et de **Deep Learning** (ex: LSTM). Cette démarche nous permettra de démontrer l'apport prédictif spécifique des variables contextuelles sur la performance globale des modèles.

<a id="2-data-presentation"></a>
### 2. Présentation du jeu de données

Le **Bike Sharing Dataset**, produit par le LIAAD (Université de Porto), compile l'historique complet du système *Capital Bikeshare* à Washington D.C. sur la période 2011-2012. Ce jeu de données se concentre sur le fichier `hour.csv` qui contient **17 379 observations horaires**, reliant le volume total de locations (`cnt`) à des indicateurs temporels précis (heure, jour férié, saison). Chaque enregistrement est enrichi de **données météorologiques normalisées** (température, humidité, vitesse du vent) et de conditions climatiques catégorielles (`weathersit`). 

In [3]:
df = pd.read_csv('../data/raw/hour.csv')

In [4]:
print(df.shape)
display(df.head(5))
display(df.tail(5))

(17379, 17)


instant      dteday  season  yr  mnth  hr  holiday  weekday  workingday  \
0        1  2011-01-01       1   0     1   0        0        6           0   
1        2  2011-01-01       1   0     1   1        0        6           0   
2        3  2011-01-01       1   0     1   2        0        6           0   
3        4  2011-01-01       1   0     1   3        0        6           0   
4        5  2011-01-01       1   0     1   4        0        6           0   

   weathersit  temp   atemp   hum  windspeed  casual  registered  cnt  
0           1  0.24  0.2879  0.81        0.0       3          13   16  
1           1  0.22  0.2727  0.80        0.0       8          32   40  
2           1  0.22  0.2727  0.80        0.0       5          27   32  
3           1  0.24  0.2879  0.75        0.0       3          10   13  
4           1  0.24  0.2879  0.75        0.0       0           1    1

instant      dteday  season  yr  mnth  hr  holiday  weekday  \
17374    17375  2012-12-31       1   1    12  19        0        1   
17375    17376  2012-12-31       1   1    12  20        0        1   
17376    17377  2012-12-31       1   1    12  21        0        1   
17377    17378  2012-12-31       1   1    12  22        0        1   
17378    17379  2012-12-31       1   1    12  23        0        1   

       workingday  weathersit  temp   atemp   hum  windspeed  casual  \
17374           1           2  0.26  0.2576  0.60     0.1642      11   
17375           1           2  0.26  0.2576  0.60     0.1642       8   
17376           1           1  0.26  0.2576  0.60     0.1642       7   
17377           1           1  0.26  0.2727  0.56     0.1343      13   
17378           1           1  0.26  0.2727  0.65     0.1343      12   

       registered  cnt  
17374         108  119  
17375          81   89  
17376          83   90  
17377          48   61  
17378          37   49

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17379 entries, 0 to 17378
Data columns (total 17 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   instant     17379 non-null  int64  
 1   dteday      17379 non-null  object 
 2   season      17379 non-null  int64  
 3   yr          17379 non-null  int64  
 4   mnth        17379 non-null  int64  
 5   hr          17379 non-null  int64  
 6   holiday     17379 non-null  int64  
 7   weekday     17379 non-null  int64  
 8   workingday  17379 non-null  int64  
 9   weathersit  17379 non-null  int64  
 10  temp        17379 non-null  float64
 11  atemp       17379 non-null  float64
 12  hum         17379 non-null  float64
 13  windspeed   17379 non-null  float64
 14  casual      17379 non-null  int64  
 15  registered  17379 non-null  int64  
 16  cnt         17379 non-null  int64  
dtypes: float64(4), int64(12), object(1)
memory usage: 2.3+ MB


<img src="../img/2_presentation_data/dico_vars.png" width="600" align="center">

<a id="3-eda"></a>
### 3. Exploration du jeu de données

#### Visualisation sommaires

In [6]:
# Conversion de la colonne 'dteday' en format datetime
df['dteday'] = pd.to_datetime(df['dteday'])
# Création de la variable 'time' (Date + Heure)
df['time'] = df['dteday'] + pd.to_timedelta(df['hr'], unit='h')
df = df.set_index('time')  # 'time' comme l'index du DataFrame
# Exploitation du timestamp
df['day_name'] = df['dteday'].dt.day_name()   # Nom du jour 
df['month_name'] = df['dteday'].dt.month_name() 
df['year_name'] = df['dteday'].dt.year             
print(df.index)

DatetimeIndex(['2011-01-01 00:00:00', '2011-01-01 01:00:00',
               '2011-01-01 02:00:00', '2011-01-01 03:00:00',
               '2011-01-01 04:00:00', '2011-01-01 05:00:00',
               '2011-01-01 06:00:00', '2011-01-01 07:00:00',
               '2011-01-01 08:00:00', '2011-01-01 09:00:00',
               ...
               '2012-12-31 14:00:00', '2012-12-31 15:00:00',
               '2012-12-31 16:00:00', '2012-12-31 17:00:00',
               '2012-12-31 18:00:00', '2012-12-31 19:00:00',
               '2012-12-31 20:00:00', '2012-12-31 21:00:00',
               '2012-12-31 22:00:00', '2012-12-31 23:00:00'],
              dtype='datetime64[ns]', name='time', length=17379, freq=None)


In [22]:
df['Année_str'] = df.index.year.astype(str)

fig = px.line(df, 
              x=df.index, 
              y='cnt', 
              color='Année_str',  # Séparation des couleurs par année
              title='Évolution de la demande horaire de vélos (cnt)')
fig.update_traces(line_width=0.5)
fig.update_layout(legend_title_text='Année')

fig.show()

- La série temporelle principale montre sur l'ensemble de la période une tendance croissante. On a des pics saisonniers généralement pendant les périodes hors-hiver (pics de demande pendant les mois plus chauds et des creux pendant les mois plus froids). On va analyser la série plus en détail par la suite. 
- L'année 2012 semble avoir plus de volume de demande que l'année 2011.
- En regardant, sur une semaine et donc les jours, on voit des pics hauts généralement en matinée (entre 5h et 8h problablement pour aller au travail les jours ouvrés et entre 17h et 19h pour rentrer ). Le traffic est un peu moindre les week-ends.

In [30]:
df['day_of_year'] = df.index.dayofyear + (df.index.hour / 24.0) 
df['Année'] = df.index.year.astype(str)

# Calcul des totaux 
total_2011 = df[df['Année'] == '2011']['cnt'].sum()
total_2012 = df[df['Année'] == '2012']['cnt'].sum()
# Graphique avec les 2 années et les tendances
fig = px.scatter(df, 
                 x='day_of_year', 
                 y='cnt', 
                 color='Année',
                 title="Comparaison Horaire 2011 vs 2012 (Données brutes + Tendance)",
                 trendline="lowess", 
                 trendline_options=dict(frac=0.1), 
                 opacity=0.15)

fig.update_traces(marker=dict(size=3))
fig.update_layout(
    xaxis_title="Jour de l'année", 
    yaxis_title="Nombre de locations (par heure)"
)
# Affichage des totaux sur le graphique
# Annotation pour 2011
fig.add_annotation(
    x=0.02, y=0.98, xref="paper", yref="paper", # Position relative (Haut Gauche)
    text=f"<b>Total 2011 :</b> {total_2011:,.0f}".replace(',', ' '), # Formatage 1 234 567
    showarrow=False
)
# Annotation pour 2012
fig.add_annotation(
    x=0.02, y=0.93, xref="paper", yref="paper", # Juste en dessous
    text=f"<b>Total 2012 :</b> {total_2012:,.0f}".replace(',', ' '),
    showarrow=False
)

fig.show()

In [16]:
cols = ['cnt', 'registered', 'casual']
df_long = df[cols].reset_index().melt(id_vars='time', var_name='Série', value_name='Nombre')
# Création du subplot
fig = px.scatter(df_long, 
                 x='time', 
                 y='Nombre', 
                 facet_row='Série',  
                 opacity=0.5,  
                 color='Série',     
                 title="Comparaison : Cnt, Registered, Casual")
fig.update_traces(marker=dict(size=2)) # Taille des points 
fig.update_yaxes()  #  matches=None pour des échelles indépendantes

fig.show()

L'essentiel de la demande se fait par des utilisateurs enregistrés.

In [ ]:
# Création d'une colonne combinée "Année-Mois" 
df['Year_Month'] = df.index.strftime('%Y-%m')
# Création du Boxplot
fig = px.box(df, 
             x='Year_Month', 
             y='cnt', 
             color='Année', # Colore les boîtes selon l'année pour bien distinguer les deux périodes
             title="Distribution mensuelle de la demande (Boxplots sur 24 mois)",
             labels={'Year_Month': 'Mois', 'cnt': 'Nombre de locations'})
fig.update_layout(
    xaxis_tickangle=-45, # Pivote les dates pour qu'elles ne se chevauchent pas
    showlegend=True
)
fig.show()

On constate des outliers sur certains mois en rapports avec des pics sur certains jours problablement.

In [ ]:
day_map = {0: 'Dim', 1: 'Lun', 2: 'Mar', 3: 'Mer', 4: 'Jeu', 5: 'Ven', 6: 'Sam'}
df['weekday_name'] = df['weekday'].map(day_map)

# Création de la structure des Subplots (1 ligne, 2 colonnes)
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=("Total Demande par Jour (Semaine)", "Distribution par Heure"),
    horizontal_spacing=0.15
)

# Création des graphiques
# On crée 3 jeux de graphiques (Tout, 2011, 2012) que l'on cachera/affichera ensuite

# Toutes les données (Visible par défaut)
# Graphique Gauche : Histogramme (Somme des cnt par jour)
fig.add_trace(go.Histogram(x=df['weekday_name'], y=df['cnt'], histfunc='sum', 
                           name='Total (Tout)', marker_color="#000000"), row=1, col=1)
# Graphique Droite : Boxplot (Distribution par heure)
fig.add_trace(go.Box(x=df['hr'], y=df['cnt'], 
                     name='Dist. (Tout)', marker_color="#000000"), row=1, col=2)

# Année 2011 (Caché au début -> visible=False)
df_11 = df[df['yr'] == 0]
fig.add_trace(go.Histogram(x=df_11['weekday_name'], y=df_11['cnt'], histfunc='sum', 
                           name='Total (2011)', marker_color='blue', visible=False), row=1, col=1)
fig.add_trace(go.Box(x=df_11['hr'], y=df_11['cnt'], 
                     name='Dist. (2011)', marker_color='blue', visible=False), row=1, col=2)

# Année 2012 (Caché au début -> visible=False)
df_12 = df[df['yr'] == 1]
fig.add_trace(go.Histogram(x=df_12['weekday_name'], y=df_12['cnt'], histfunc='sum', 
                           name='Total (2012)', marker_color='orange', visible=False), row=1, col=1)
fig.add_trace(go.Box(x=df_12['hr'], y=df_12['cnt'], 
                     name='Dist. (2012)', marker_color='orange', visible=False), row=1, col=2)

# Menu déroulant
fig.update_layout(
    updatemenus=[dict(
        active=0, # Le premier bouton est actif par défaut
        buttons=list([
            # Bouton 1 : Tout afficher
            dict(label="Les 2 années",
                 method="update",
                 # On rend visible les traces 0 et 1 (indices Python), et on cache les autres
                 args=[{"visible": [True, True, False, False, False, False]},
                       {"title": "Analyse Globale (2011-2012)"}]),
            
            # Bouton 2 : 2011
            dict(label="2011 Uniquement",
                 method="update",
                 # On rend visible les traces 2 et 3
                 args=[{"visible": [False, False, True, True, False, False]},
                       {"title": "Analyse Année 2011"}]),
            
            # Bouton 3 : 2012
            dict(label="2012 Uniquement",
                 method="update",
                 # On rend visible les traces 4 et 5
                 args=[{"visible": [False, False, False, False, True, True]},
                       {"title": "Analyse Année 2012"}]),
        ]),
        x=0.0, y=1.15, # Position du menu (en haut à gauche)
        showactive=True
    )],
    title="Analyse Globale (2011-2012)",
    showlegend=False # On enlève la légende car redondante avec les titres
)

# Ordre des jours (sinon c'est alphabétique)
order_days = ['Lun', 'Mar', 'Mer', 'Jeu', 'Ven', 'Sam', 'Dim']
fig.update_xaxes(categoryorder='array', categoryarray=order_days, row=1, col=1)

fig.show()

- Nos observations précédentes restent valables. On va maintenant observer la décomposition de la série principale, avant de passer aux analyses statistiques.

In [45]:
# On somme les locations horaires pour avoir un total par jour (car par heure c'est chaud de visualiser)
df_daily = df['cnt'].resample('D').sum()

# Calcul et plot de la décomposition
# model='additive' : Car l'amplitude des variations saisonnières semble constante
# period=7 : Car on regarde des données journalières et on cherche le pattern hebdomadaire
decomposition = seasonal_decompose(df_daily, model='additive', period=7)
fig = plot_seasonal_decompose(decomposition, title="Décomposition de la demande (Données Journalières)")
fig.show()

#### Analyse univariée

#### Analyse multivariée